In [1]:
!python -V
!which python

Python 3.9.6
/Users/satori/.pyenv/versions/nemo/bin/python


In [2]:
import nemo

In [3]:
import nemo.collections.asr as nemo_asr


[NeMo W 2021-08-11 14:00:53 optimizers:47] Apex was not found. Using the lamb optimizer will error out.
[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /Users/satori/nltk_data...
[nltk_data]   Unzipping taggers/averaged_perceptron_tagger.zip.
[nltk_data] Downloading package cmudict to /Users/satori/nltk_data...
[nltk_data]   Unzipping corpora/cmudict.zip.
[NeMo W 2021-08-11 14:01:49 experimental:27] Module <class 'nemo.collections.asr.data.audio_to_text_dali._AudioTextDALIDataset'> is experimental, not ready for production and is not fully supported. Use at your own risk.


In [6]:
golos = nemo_asr.models.EncDecCTCModel.restore_from("QuartzNet15x5_golos.nemo")

[NeMo W 2021-08-11 14:10:53 modelPT:130] If you intend to do training or fine-tuning, please call the ModelPT.setup_training_data() method and provide a valid configuration file to setup the train data loader.
    Train config : 
    manifest_filepath: train/golos_and_mcv.jsonl
    sample_rate: 16000
    labels:
    - ' '
    - а
    - б
    - в
    - г
    - д
    - е
    - ж
    - з
    - и
    - й
    - к
    - л
    - м
    - н
    - о
    - п
    - р
    - с
    - т
    - у
    - ф
    - х
    - ц
    - ч
    - ш
    - щ
    - ъ
    - ы
    - ь
    - э
    - ю
    - я
    batch_size: 64
    trim_silence: false
    max_duration: 20.0
    min_duration: 0.1
    num_workers: 20
    shuffle: true
    is_tarred: false
    tarred_audio_filepaths: null
    tarred_shard_strategy: scatter
    parser: ru
    
[NeMo W 2021-08-11 14:10:53 modelPT:137] If you intend to do validation, please call the ModelPT.setup_validation_data() or ModelPT.setup_multiple_validation_data() method and provide a

[NeMo I 2021-08-11 14:10:53 features:252] PADDING: 16
[NeMo I 2021-08-11 14:10:53 features:269] STFT using torch
[NeMo I 2021-08-11 14:10:54 save_restore_connector:143] Model EncDecCTCModel was successfully restored from /Users/satori/Projects/mlprojects/nemo/QuartzNet15x5_golos.nemo.


In [9]:
!pip install datasets

     |████████████████████████████████| 264 kB 62 kB/s eta 0:00:01
     |████████████████████████████████| 17.6 MB 56 kB/s eta 0:00:01
     |████████████████████████████████| 128 kB 57 kB/s eta 0:00:01
     |████████████████████████████████| 86 kB 68 kB/s eta 0:00:01


In [10]:
from datasets import load_dataset

In [12]:
LANG_ID = "ru"

In [13]:
test_dataset = load_dataset("common_voice", LANG_ID)

Downloading:   0%|          | 0.00/4.36k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/10.2k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/3.66G [00:00<?, ?B/s]

0 examples [00:00, ? examples/s]

0 examples [00:00, ? examples/s]

0 examples [00:00, ? examples/s]

0 examples [00:00, ? examples/s]

0 examples [00:00, ? examples/s]

Dataset common_voice downloaded and prepared to /Users/satori/.cache/huggingface/datasets/common_voice/ru/6.1.0/078d412587e9efeb0ae2e574da99c31e18844c496008d53dc5c60f4159ed639b. Subsequent calls will reuse this data.


In [15]:
test_dataset = load_dataset("common_voice", LANG_ID, split=f"test[:{5}]")

Reusing dataset common_voice (/Users/satori/.cache/huggingface/datasets/common_voice/ru/6.1.0/078d412587e9efeb0ae2e574da99c31e18844c496008d53dc5c60f4159ed639b)


In [16]:
test_dataset

Dataset({
    features: ['client_id', 'path', 'sentence', 'up_votes', 'down_votes', 'age', 'gender', 'accent', 'locale', 'segment'],
    num_rows: 5
})

In [42]:
import librosa
import IPython.display as ipd
from pydub import AudioSegment
import os
from IPython.core.display import display

In [45]:
wav_files = []
for audio in test_dataset['path']:
    base = os.path.basename(audio)
    base = os.path.splitext(base)[0]
    wav_file = f"./{base}.wav"
    sound = AudioSegment.from_mp3(audio)
    sound.export(wav_file, format="wav")
    wav_files.append(wav_file)
    display(ipd.Audio(wav_file))

In [46]:
results = golos.transcribe(wav_files)
print(results)

Transcribing:   0%|          | 0/2 [00:00<?, ?it/s]

['он работать а ее не удержатникак бегает за кляшем каждого бульварника', 'если не будет возражений я буду считать что ассамблея согласна с этим предложением', 'полестинцам необходимо сначала установить сни мир феврелим а закем добиваьция признания государств нноски', 'у меня было такое чувство что что то такое очень важное я прибавляю', 'только вряд ля поймят']
